# THIS CODE IS NOT STRUCTURE. IT CONTAINS USEFUL PIECES FOR DEBUGGING ERRORS IN THE CAD FILE. IT COULD BE PRACTICAL TO BUILD AN ERROR FINDING CODE

In [1]:
import geopandas as gpd
from shapely.geometry import Point, Polygon
import pandas as pd
import numpy as np
import math
import ray

In [2]:
geom=gpd.read_file('geometry/220429-VOLPE Clean03.dxf')

In [3]:
nodes_df = pd.read_csv('nodes_df.csv')

In [13]:
#Node disconnected is 5373 from the entity handle 95152 (elevator)
nodes_95152 = nodes_df[nodes_df['EntityHandle']=='95152']

In [15]:
nodes_95152

Unnamed: 0    id              x             y     z type_of_entity  \
3001        3001  5373  768096.399682  2.958520e+06  65.0      ELEVATORS   
3064        3064  5436  768096.399682  2.958520e+06  65.0           path   

     EntityHandle  
3001        95152  
3064        95152

In [31]:
#The elevator to analise is in 65.0 floor. Geom taken is just that floor.
geom_65 = geom[geom['geometry'].apply(lambda x: x.coords[0][2]==65.0)]

In [32]:
#From geom_65 just the elevators are saved
set_elevators = {'ELEVATORS'}
set_alleys = {'ALLEY-ELEVATOR','ALLEY1'}
geom_65_elevators = geom_65[geom_65['Layer'].apply(lambda x: x in set_elevators)]
geom_65_alleys = geom_65[geom_65['Layer'].apply(lambda x: x in set_alleys)]
#Just those geometries with more than two points are saved
geom_65_elevators = geom_65_elevators[geom_65_elevators['geometry'].apply(lambda x: len(x.coords)>2)]
#Turn linestrings into polygons
geom_65_elevators['geometry'] =  geom_65_elevators['geometry'].apply(lambda x: Polygon(x.coords) if len(x.coords)>2 else x)
#Take the entity handle to study
geom_95152 = geom_65_elevators[geom_65_elevators['EntityHandle'].apply(lambda x: x=='95152')]

In [33]:
# CHECK IF A POINT IS ALREADY IN A DATAFRAME AND RETURN THE POINT IN THE DATAFRAME IF TRUE 
def check_point_polygons(coordinates,geom_polygons):
    for index_p, element_p in enumerate(geom_polygons['geometry']):
        if (Point(coordinates).within(element_p)):
            return True,index_p
    return False,None

In [44]:
# CHECK IF ALLEYS ARE IN ELEVATORS
for index in np.arange(len(geom_65_alleys)):
    #if index%10 == 0: print("{} of {} points from alleys evaluated".format(index,len(geom_alleys)))     
    element_to_evaluate = geom_65_alleys['geometry'].iloc[index].coords
    for index_e,point_e in enumerate(element_to_evaluate):
        # NODES ARE CHECKED TO BE IN ANY OF THE POLYGONS
        contained_in_p,index_p = check_point_polygons(point_e,geom_95152)
        entity_handler_container = None
        if(contained_in_p):
            print("{} is cointained".format(geom_65_alleys.iloc[index]))


Layer                                              ALLEY-ELEVATOR
PaperSpace                                                   None
SubClasses                                                   None
Linetype                                                     None
EntityHandle                                                95203
Text                                                         None
geometry        LINESTRING Z (768097.5243239894 2958519.691925...
Name: 4426, dtype: object is cointained


In [52]:
# CHECK WHICH NODESDF FALL INSIDE THE POLIGON   
for index_e,point_e in enumerate(nodes_df.values):
    # NODES ARE CHECKED TO BE IN ANY OF THE POLYGONS
    coords_e = [point_e[2],point_e[3],point_e[4]]
    if(coords_e[2]==65.0):
        contained_in_p,index_p = check_point_polygons(coords_e,geom_95152)
        entity_handler_container = None
        if(contained_in_p):
            print("{} is cointained".format(point_e))

[3001 5373 768096.3996816466 2958520.3515861486 65.0 'ELEVATORS' '95152'] is cointained
[3064 5436 768096.3996816463 2958520.351586151 65.0 'path' '95152'] is cointained


In [46]:
for index_e,point_e in enumerate(nodes_df.values):
    print(point_e)

[0 0 768036.7399632288 2957844.410536579 0.0 'Entrance' '938D5']
[1 1 768038.8703454463 2957848.598884073 0.0 'Entrance' '93903']
[2 2 768045.1745871041 2957838.641894846 0.0 'Entrance' '938D6']
[3 3 768046.7799917834 2957844.277743788 0.0 'Entrance' '93903']
[4 4 768052.6334838751 2957835.914188761 0.0 'Entrance' '938D7']
[5 5 768054.6896381201 2957839.956603502 0.0 'Entrance' '93903']
[6 6 768060.3425778784 2957831.198761077 0.0 'Entrance' '938D8']
[7 7 768062.5992844572 2957835.635463217 0.0 'Entrance' '93903']
[8 8 768041.7500570158 2957855.556132301 0.0 'Entrance' '93903']
[9 9 768048.152652349 2957851.972690786 0.0 'Entrance' '93903']
[10 10 768063.1053761501 2957843.603864012 0.0 'Entrance' '93903']
[11 11 768068.7979884351 2957840.417789906 0.0 'Entrance' '93903']
[12 12 768050.7348149517 2957842.117173645 0.0 'Entrance' '93903']
[13 13 768054.0942176557 2957847.749593915 0.0 'Entrance' '93903']
[14 14 768057.0896916735 2957868.388408171 0.0 'Entrance' '93903']
[15 15 768072.75